Pasos para hacer funcionar el codigo :)
Primero instalar BerTopic pip install bertopic

In [2]:
from bertopic import BERTopic
import json
import pandas as pd


/Users/jorgealejandro/Documents/Dev/AI/topic modeling/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Aca cargamos el archivo json y lo asignamos a la variable f
luego medimos el tamano, en un siguiente codigo el json deberia de descargarse de la API de CosmosDB
de BAC GPT

Si el dataset es muy grande y estamos realizando pruebas ppodriamos limitar la cantidad de documentos con la siguiente linea de codigo:
docs = json.load(f)["descriptions"][:"cantidad de documentos a cargar"]

In [3]:
with open("vol7.json", "r", encoding="utf-8") as f:
    docs = json.load(f)["descriptions"]
len(docs)

21747

Imprimimos uno de prueba, el indice 0 de 21747

In [4]:
docs[0]

"An ANCYL member who was shot and severely injured by SAP members at Lephoi, Bethulie, Orange Free State (OFS) on 17 April 1991. Police opened fire on a gathering at an ANC supporter's house following a dispute between two neighbours, one of whom was linked to the ANC and the other to the SAP and a councillor."

Seleccionamos un modelo para transformar nuestro texto en embeddings para represetar numericamente la semantica de nuestro texto

In [5]:
topic_model = BERTopic(embedding_model="all-MiniLM-L6-v2")

Cargamos todo nuestro dataset al modelo de emmbedigs y lo transformamos

In [6]:
topics, probs = topic_model.fit_transform(docs)

OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitl

Vemos la informacion de los topicos
Verificamos la columna Topic|Count|Name
Topic: nos da un valor numerico, cuando es negativo son los outliers (valores que no son normales) son los que normalmente queremos ingnorar
probablemente tengamos que ver estos documentos un poco mas de cerca y analizarlos nuevamente para entender porque sus valores son atipicos.

ejemplo -1_esto_es_una_prueba

Count: es el numero de documentos que son de la categoria topic 

Name: es un poco de la informacion que tenemos de la categorizacion de topic siguiendo el ejemplo anterior -1_esto_es_una_prueba 
Primero tenemos el numero de topico seguido del top 4 palabras que representan el documento y estas palabras nos dan una idea de lo que se habla dentro

Estas cuatro palabras dan una idea general de lo que tiene dentro el documento pero podemos darle un significado mas profundo a cada documento individualmente(filas)

In [7]:
topic_model.get_topic_info()

Topic  Count                                         Name  \
0       -1   5244                   -1_shot_anc_supporters_his   
1        0    935          0_detained_tortured_arrested_months   
2        1    402          1_udf_detained_tortured_regulations   
3        2    341                   2_stabbed_death_1991_natal   
4        3    254  3_bophuthatswana_taung_zeerust_leeuwfontein   
..     ...    ...                                          ...   
409    408     11                408_coup_tdf_soldier_soldiers   
410    409     11      409_iec_distributing_pamphlets_reprisal   
411    410     10              410_rent_boycott_sparked_bakkie   
412    411     10         411_nelson_inkatha_mandela_njobokazi   
413    412     10          412_manyelo_sisters_katlehong_niece   

                                        Representation  \
0    [shot, anc, supporters, his, was, allegedly, t...   
1    [detained, tortured, arrested, months, detenti...   
2    [udf, detained, tortured, regulations, emergen...   
3    [stabbed, death, 1991, natal, to, supporter, a...   
4    [bophuthatswana, taung, zeerust, leeuwfontein,...   
..                                                 ...   
409  [coup, tdf, soldier, soldiers, attempted, 095,...   
410  [iec, distributing, pamphlets, reprisal, priva...   
411  [rent, boycott, sparked, bakkie, restore, evic...   
412  [nelson, inkatha, mandela, njobokazi, release,...   
413  [manyelo, sisters, katlehong, niece, daughter,...   

                                   Representative_Docs  
0    [An Inkatha supporter who had his house in Mpu...  
1    [A student leader who was detained in Bloemfon...  
2    [A UDF supporter who was detained in Bloemfont...  
3    [An ANC supporter who was stabbed to death by ...  
4    [Was severely beaten by members of the Bophuth...  
..                                                 ...  
409  [A Transkei Defence Force (TDF) soldier who wa...  
410  [An ANC supporter who was shot dead by IFP sup...  
411  [Was shot dead by alleged members of the SAP i...  
412  [An Inkatha supporter who had her house burnt ...  
413  [Was shot and killed when her family was attac...  

[414 rows x 5 columns]

Dandole un significado mas entendible a cada fila, verificamos todas las palabras del documento(fila)
Cuando utilizamos embbedings no necesitamos limpiar identificando las stop words o hacer el preprocesamiento quitando el ruido que es donde realmente nos ayuda Bert

In [8]:
topic_model.get_topic(1)

[('udf', 0.014686706043858445),
 ('detained', 0.011094118973769765),
 ('tortured', 0.009464293148160864),
 ('regulations', 0.00945839928207848),
 ('emergency', 0.008992668231779147),
 ('under', 0.008929774325487031),
 ('months', 0.00832187440223916),
 ('1986', 0.007792455499789004),
 ('cape', 0.00760303076736747),
 ('arrested', 0.0074268625935827205)]

La pregunta seria que documentos estan en este topico de arriba?
Lo hacemos con la siguiente linea de codigo, ya que el modelo guarda por nosotros esta informacion

Esto devuelve el top 3 de documentos que se pueden representan ese cluster

In [9]:
topic_model.get_representative_docs(1)

['A UDF supporter who was detained in Bloemfontein in June 1986, under emergency regulations. He was held in custody for two months, during which he was severely assaulted by members of the SAP. See police brutality. ',
 'A UDF supporter who was severely beaten while in detention by named and other members of the SAP in Kimberley, Cape, in June 1986. He was then held under emergency regulations for three months. See police brutality.',
 'A UDF activist who was arrested and tortured by members of the SAP, and detained for several months under emergency regulations in Richmond, Cape, in 1986. See police brutality. ']

Si quisieramos ver todos los topicos y no solo un documento como en la linea anterior?

podriamos insertar todos los topicos que encontramos cuando entrenamos bertTopic Model y convertirlo en un dataFrame

In [10]:
#el data frame tendra dos columnas, una donde tendremos el numero de topico al que pertenece y la segunda el documento que esta representado por ese topico
df = pd.DataFrame({"topic": topics, "document":docs})
df

topic                                           document
0         55  An ANCYL member who was shot and severely inju...
1         31  A member of the SADF who was severely injured ...
2         64  A member of QIBLA who disappeared in September...
3         21  A COSAS supporter who was kicked and beaten wi...
4          8  Was shot and blinded in one eye by members of ...
...      ...                                                ...
21742      6  One of two South African Police (SAP) members ...
21743     -1  An ANC supporter who was shot dead by a named ...
21744     11  Was shot dead in Tokoza, Transvaal, on 22 May ...
21745    229  His home was lost in an arson attack by Witdoe...
21746    408  A Transkei Defence Force (TDF) soldier who was...

[21747 rows x 2 columns]

De esta forma podemos analizar los topico y podemos estructurarlos

ahora visualizemoslo en clusters

In [11]:
topic_model.visualize_topics()

Esta es una represntacion de los topicos en 2D que muestra en un espacio como los topicos estan distribuidos, los clusters mas cercanos entre si son semanticamente mas parecidos y vicebersa 

In [12]:
topic_model.visualize_barchart()